In [1]:
import re
import geopandas as gpd
from shapely.geometry import Point
try:
    from shapely import make_valid
except Exception:
    make_valid = None

import folium
from folium import GeoJson, FeatureGroup
from folium.plugins import MarkerCluster
import json

In [2]:
# --- helpers ---
def fix_valid(gdf):
    if make_valid is not None:
        gdf["geometry"] = gdf.geometry.apply(make_valid)
    else:
        gdf["geometry"] = gdf.buffer(0)
    return gdf

def to_wgs84(gdf):
    if gdf.crs is None:
        raise ValueError("Layer has no CRS. Set the correct CRS before reprojecting.")
    return gdf.to_crs(epsg=4326) if gdf.crs.to_epsg() != 4326 else gdf

def read_fix(path):
    g = gpd.read_file(path)
    g = fix_valid(g)
    g = to_wgs84(g)
    return g


def year_from_path(path):
    m = re.search(r"(19|20)\d{2}", path)
    return int(m.group(0)) if m else None


In [3]:
poly_path = r"d:/Users/ivan.cavalcanti/Documents/Projects/mapeando_cep/data/SP_Municipios_2024/SP_Municipios_2024.shp"
poly = read_fix(poly_path)
mun = poly[poly["NM_MUN"] == "Jundiaí"].copy()
if mun.empty:
    raise ValueError("Municipality 'Jundiaí' not found in NM_MUN.")
mun = mun.dissolve()

In [4]:
minx, miny, maxx, maxy = mun.total_bounds
center = [(miny + maxy) / 2, (minx + maxx) / 2]  # [lat, lon]

In [5]:
m = folium.Map(location=center, zoom_start=12, tiles=None)
folium.TileLayer(
    tiles="https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}",
    attr="&copy; Esri, Maxar, Earthstar Geographics, and the GIS User Community",
    name="Esri World Imagery",
    overlay=False,
    control=False,
).add_to(m)


In [6]:
folium.map.CustomPane("mun_halo", z_index=650).add_to(m)
folium.map.CustomPane("mun_line", z_index=651).add_to(m)
GeoJson(
    mun.__geo_interface__,
    name=None,
    pane="mun_halo",
    style_function=lambda f: {"color": "#000", "weight": 8, "opacity": 0.25, "fillOpacity": 0},
    tooltip="Município de Jundiaí",
).add_to(m)
GeoJson(
    mun.__geo_interface__,
    name=None,
    pane="mun_line",
    style_function=lambda f: {
        "color": "#FFD700",
        "weight": 3,
        "dashArray": "6,4",
        "fillColor": "#FFF59D",
        "fillOpacity": 0.15,
    },
    tooltip="Município de Jundiaí",
).add_to(m)

In [7]:
m

In [22]:
# three_year_map.py
import re, json
import geopandas as gpd
import folium
from folium import FeatureGroup, GeoJson
from folium.plugins import MarkerCluster

try:
    from shapely import make_valid  # shapely >= 2.0
except Exception:
    make_valid = None

# -------- helpers --------
def fix_valid(gdf: gpd.GeoDataFrame) -> gpd.GeoDataFrame:
    if make_valid is not None:
        gdf["geometry"] = gdf.geometry.apply(make_valid)
    else:
        gdf["geometry"] = gdf.buffer(0)
    return gdf

def to_wgs84(gdf: gpd.GeoDataFrame) -> gpd.GeoDataFrame:
    if gdf.crs is None:
        raise ValueError("CRS is missing. Set it on the shapefile before reprojecting.")
    return gdf.to_crs(4326) if gdf.crs.to_epsg() != 4326 else gdf

def year_from_path(path: str):
    m = re.search(r"(19|20)\d{2}", path)
    return int(m.group(0)) if m else None

def load_urban_layer(path: str) -> tuple[gpd.GeoDataFrame, str]:
    g = gpd.read_file(path)
    g = fix_valid(g)
    g = to_wgs84(g)

    if "soil_use" not in g.columns:
        g["soil_use"] = "urbano"

    yr = None
    if "year" in g.columns and g["year"].notna().any():
        try:
            yr = int(g["year"].iloc[0])
        except Exception:
            pass
    if yr is None:
        yr = year_from_path(path)
    if yr is None:
        raise ValueError(f"Could not determine year for {path}")
    g["year"] = int(yr)

    g = g[g["soil_use"].astype(str).str.lower().eq("urbano")].copy()
    if g.empty:
        raise ValueError(f"No 'urbano' features in {path}")

    return g, str(yr)

# -------- config --------
PATH_2000 = "./data/soil_use_2000.shp"
PATH_2010 = "./data/soil_use_2010.shp"
PATH_2023 = "./data/soil_use_2023.shp"
YEAR_COLS = {"2000": "#e3d917", "2010": "#e32f17", "2023": "#62130a"}

# -------- load layers --------
g2000, y2000 = load_urban_layer(PATH_2000)
g2010, y2010 = load_urban_layer(PATH_2010)
g2023, y2023 = load_urban_layer(PATH_2023)

# combined bounds
minx = min(g2000.total_bounds[0], g2010.total_bounds[0], g2023.total_bounds[0])
miny = min(g2000.total_bounds[1], g2010.total_bounds[1], g2023.total_bounds[1])
maxx = max(g2000.total_bounds[2], g2010.total_bounds[2], g2023.total_bounds[2])
maxy = max(g2000.total_bounds[3], g2010.total_bounds[3], g2023.total_bounds[3])
center = [(miny + maxy) / 2, (minx + maxx) / 2]  # [lat, lon]

# -------- map --------
m = folium.Map(location=center, zoom_start=12, tiles=None)

# base layers WITH names (so LayerControl shows)
folium.TileLayer("OpenStreetMap", name="OSM", overlay=False, control=True).add_to(m)
folium.TileLayer(
    tiles="https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}",
    attr="Esri, Maxar, Earthstar Geographics",
    name="Satélite (Esri)",
    overlay=False, control=True
).add_to(m)


def add_year_layer(gdf: gpd.GeoDataFrame, year_str: str, show: bool):
    fg = FeatureGroup(name=year_str, show=show)
    GeoJson(
        data=json.loads(gdf.to_json()),
        name=None,
        style_function=lambda f, c=YEAR_COLS.get(year_str, "#333333"): {
            "color": c, "fillColor": c, "fillOpacity": 0.5, "weight": 1
        },
        highlight_function=lambda f: {"weight": 2},
        tooltip=folium.GeoJsonTooltip(fields=["year"], aliases=["Ano:"]),
    ).add_to(fg)
    fg.add_to(m)

# add overlays (show only latest by default)
add_year_layer(g2023, y2023, show=True)
add_year_layer(g2010, y2010, show=True)
add_year_layer(g2000, y2000, show=True)

PARKS_PATH = r"d:/Users/ivan.cavalcanti/Documents/Projects/areas-verdes/data/Geojundiai/L_8683-2016_m13_parques-municipais.shp"  # <-- change to your file

parques = gpd.read_file(PARKS_PATH)
parques = fix_valid(parques)
parques = to_wgs84(parques)

fg_parks = FeatureGroup(name="Parques", show=True)
icon = folium.Icon(color="green", icon="tree", prefix="fa")

for _, row in parques.iterrows():
    geom = row.geometry
    if geom is None or geom.is_empty:
        continue
    pt = geom if geom.geom_type == "Point" else geom.centroid
    folium.Marker(
        location=[pt.y, pt.x],
        tooltip=str(row.get("nome", "")),
        popup=str(row.get("nome", "")),
        icon=icon,
    ).add_to(fg_parks)

fg_parks.add_to(m)



mun = gpd.read_file(r"d:/Users/ivan.cavalcanti/Documents/Projects/mapeando_cep/data/SP_Municipios_2024/SP_Municipios_2024.shp")
mun = fix_valid(mun)
mun = to_wgs84(mun)
mun = mun[mun["NM_MUN"] == "Jundiaí"].copy()
mun = mun.dissolve()  # single footprint
folium.map.CustomPane("mun_halo", z_index=580).add_to(m)
folium.map.CustomPane("mun_line", z_index=590).add_to(m)

# make panes non-interactive so they don't steal hover/clicks
m.get_root().html.add_child(folium.Element("""
<style>
.mun_halo-pane, .mun_line-pane { pointer-events: none; }
</style>
"""))

# halo (no control entry)
folium.GeoJson(
    data=json.loads(mun.to_json()),
    name=None,
    control=False,              # <-- keep OUT of LayerControl
    pane="mun_halo",
    style_function=lambda f: {"color": "#000000", "weight": 8, "opacity": 0.25, "fillOpacity": 0.0},
).add_to(m)

# outline + soft fill (no control entry)
folium.GeoJson(
    data=json.loads(mun.to_json()),
    name=None,
    control=False,              # <-- keep OUT of LayerControl
    pane="mun_line",
    style_function=lambda f: {
        "color": "#FFD700", "weight": 3, "dashArray": "6,4",
        "fillColor": "#FFF59D", "fillOpacity": 0.15
    },
).add_to(m)




# control + bounds
folium.LayerControl(position="topright", collapsed=False).add_to(m)
m.fit_bounds([[miny, minx], [maxy, maxx]])

In [3]:
mun

geometry   CD_MUN   NM_MUN  \
0  POLYGON ((-46.85434 -23.20726, -46.85425 -23.2...  3525904  Jundiaí   

   CD_RGI   NM_RGI CD_RGINT  NM_RGINT CD_UF      NM_UF SIGLA_UF CD_REGIA  \
0  350039  Jundiaí     3510  Campinas    35  São Paulo       SP        3   

  NM_REGIA SIGLA_RG CD_CONCU    NM_CONCU  AREA_KM2  
0  Sudeste       SE  3525904  Jundiaí/SP   431.204

In [23]:
m

In [7]:

for cand in ["nome", "NOME", "Name", "name", "NM_PARQUE", "NM", "TITULO"]:
    if cand in parques.columns:
        parques["label"] = parques[cand].astype(str)
        break
else:
    parques["label"] = "Parque"

In [9]:
fg_parks = FeatureGroup(name="Parques", show=True)

In [15]:

parques = gpd.read_file(PARKS_PATH)
parques = fix_valid(parques)
parques = to_wgs84(parques)

In [13]:
 parques["nome"] = "Parque"

In [14]:
parques

nome   cod                     geometry
0   Parque  None  POINT (-46.96671 -23.18531)
1   Parque  None    POINT (-46.9066 -23.1656)
2   Parque  None   POINT (-46.88823 -23.1898)
3   Parque  None   POINT (-46.8743 -23.19372)
4   Parque  None  POINT (-46.85484 -23.18412)
5   Parque  None  POINT (-46.91505 -23.14406)
6   Parque  None  POINT (-46.87244 -23.19518)
7   Parque  None   POINT (-46.88007 -23.2169)
8   Parque  None   POINT (-46.89556 -23.2075)
9   Parque    02   POINT (-46.8872 -23.15441)
10  Parque    07  POINT (-46.91959 -23.10967)
11  Parque    06  POINT (-46.89861 -23.19177)
12  Parque    04    POINT (-46.96102 -23.188)
13  Parque    01  POINT (-46.89827 -23.17383)
14  Parque    05   POINT (-46.9554 -23.15774)
15  Parque    03  POINT (-46.89427 -23.16304)
16  Parque    08  POINT (-46.86043 -23.21503)
17  Parque    09  POINT (-46.93132 -23.13946)
18  Parque    10  POINT (-46.92901 -23.13611)

In [10]:
# two_year_map.py
import re, json
import geopandas as gpd
import folium
from folium import FeatureGroup, GeoJson

try:
    from shapely import make_valid  # shapely >= 2.0
except Exception:
    make_valid = None

# -------- helpers --------
def fix_valid(gdf: gpd.GeoDataFrame) -> gpd.GeoDataFrame:
    if make_valid is not None:
        gdf["geometry"] = gdf.geometry.apply(make_valid)
    else:
        gdf["geometry"] = gdf.buffer(0)
    return gdf

def to_wgs84(gdf: gpd.GeoDataFrame) -> gpd.GeoDataFrame:
    if gdf.crs is None:
        raise ValueError("CRS is missing on a layer. Set it before reprojecting.")
    return gdf.to_crs(4326) if gdf.crs.to_epsg() != 4326 else gdf

def year_from_path(path: str):
    m = re.search(r"(19|20)\d{2}", path)
    return int(m.group(0)) if m else None

def load_urban_layer(path: str) -> tuple[gpd.GeoDataFrame, str]:
    g = gpd.read_file(path)
    g = fix_valid(g)
    g = to_wgs84(g)

    if "soil_use" not in g.columns:
        g["soil_use"] = "urbano"

    yr = None
    if "year" in g.columns and g["year"].notna().any():
        try:
            yr = int(g["year"].iloc[0])
        except Exception:
            pass
    if yr is None:
        yr = year_from_path(path)
    if yr is None:
        raise ValueError(f"Could not determine year for {path}")
    g["year"] = int(yr)

    g = g[g["soil_use"].astype(str).str.lower().eq("urbano")].copy()
    if g.empty:
        raise ValueError(f"No 'urbano' features in {path}")

    return g, str(yr)

# -------- config (set your paths) --------
PATH_2010 = "./data/soil_use_2010.shp"
PATH_2023 = "./data/soil_use_2023.shp"
YEAR_COLS = {"2010": "#e32f17", "2023": "#62130a"}

# -------- load layers --------
g2010, y2010 = load_urban_layer(PATH_2010)
g2023, y2023 = load_urban_layer(PATH_2023)

# bounds & center from combined extent
minx = min(g2010.total_bounds[0], g2023.total_bounds[0])
miny = min(g2010.total_bounds[1], g2023.total_bounds[1])
maxx = max(g2010.total_bounds[2], g2023.total_bounds[2])
maxy = max(g2010.total_bounds[3], g2023.total_bounds[3])
center = [(miny + maxy) / 2, (minx + maxx) / 2]  # [lat, lon]

# -------- map --------
m = folium.Map(location=center, zoom_start=12, tiles=None)

# Base layers WITH names so the control appears
folium.TileLayer(
    tiles="https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}",
    attr="Esri, Maxar, Earthstar Geographics",
    name="Satélite (Esri)",
    overlay=False,
    control=True
).add_to(m)
folium.TileLayer("OpenStreetMap", name="OSM", overlay=False, control=True).add_to(m)

# 2010 overlay
fg10 = FeatureGroup(name=y2010, show=False)  # hidden by default
GeoJson(
    data=json.loads(g2010.to_json()),
    name=None,
    style_function=lambda f, c=YEAR_COLS.get(y2010, "#333333"): {
        "color": c, "fillColor": c, "fillOpacity": 0.5, "weight": 1
    },
    highlight_function=lambda f: {"weight": 2},
    tooltip=folium.GeoJsonTooltip(fields=["year"], aliases=["Ano:"]),
).add_to(fg10)
fg10.add_to(m)

# 2023 overlay (shown by default)
fg23 = FeatureGroup(name=y2023, show=True)
GeoJson(
    data=json.loads(g2023.to_json()),
    name=None,
    style_function=lambda f, c=YEAR_COLS.get(y2023, "#333333"): {
        "color": c, "fillColor": c, "fillOpacity": 0.5, "weight": 1
    },
    highlight_function=lambda f: {"weight": 2},
    tooltip=folium.GeoJsonTooltip(fields=["year"], aliases=["Ano:"]),
).add_to(fg23)
fg23.add_to(m)

# Layer control AFTER adding layers
folium.LayerControl(position="topright", collapsed=False).add_to(m)

# Fit to combined bounds
m.fit_bounds([[miny, minx], [maxy, maxx]])

In [ ]:
m

In [8]:
import re, json
import geopandas as gpd
import folium
from folium import FeatureGroup, GeoJson

try:
    from shapely import make_valid  # shapely >= 2.0
except Exception:
    make_valid = None

# ---------- config ----------
SHAPE_PATH = "./data/soil_use_2010.shp"  # <--- change to your file
YEAR_COLOR = "#e32f17"                   # color for this year

# ---------- helpers ----------
def fix_valid(gdf: gpd.GeoDataFrame) -> gpd.GeoDataFrame:
    if make_valid is not None:
        gdf["geometry"] = gdf.geometry.apply(make_valid)
    else:
        gdf["geometry"] = gdf.buffer(0)
    return gdf

def to_wgs84(gdf: gpd.GeoDataFrame) -> gpd.GeoDataFrame:
    if gdf.crs is None:
        raise ValueError("CRS is missing. Set the correct CRS on your shapefile before reprojecting.")
    return gdf.to_crs(4326) if gdf.crs.to_epsg() != 4326 else gdf

def year_from_path(path: str) -> int | None:
    m = re.search(r"(19|20)\d{2}", path)
    return int(m.group(0)) if m else None

# ---------- load + prep ----------
g = gpd.read_file(SHAPE_PATH)
g = fix_valid(g)
g = to_wgs84(g)

# ensure attributes
if "soil_use" not in g.columns:
    g["soil_use"] = "urbano"
yr = None
if "year" in g.columns and g["year"].notna().any():
    try:
        yr = int(g["year"].iloc[0])
    except Exception:
        pass
if yr is None:
    yr = year_from_path(SHAPE_PATH) or 0
g["year"] = int(yr)

# keep only urbano
g = g[g["soil_use"].astype(str).str.lower().eq("urbano")].copy()
if g.empty:
    raise SystemExit(f"No 'urbano' features found in {SHAPE_PATH}. "
                     "Check the 'soil_use' values or adjust the filter.")

# bounds & center (minx, miny, maxx, maxy)
minx, miny, maxx, maxy = g.total_bounds
center = [(miny + maxy) / 2, (minx + maxx) / 2]  # [lat, lon]

# ---------- map ----------
m = folium.Map(location=center, zoom_start=12, tiles=None)

# Base layers WITH names so the control appears
folium.TileLayer(
    tiles="https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}",
    attr="Esri, Maxar, Earthstar Geographics",
    name="Satélite (Esri)",
    overlay=False,
    control=True
).add_to(m)
folium.TileLayer("OpenStreetMap", name="OSM", overlay=False, control=True).add_to(m)

# Overlay for this year (FeatureGroup so it shows in the control)
fg = FeatureGroup(name=str(yr), show=True)
geojson_data = json.loads(g.to_json())  # plain dict → avoids dtype issues

GeoJson(
    data=geojson_data,
    name=None,  # group carries the name
    style_function=lambda feature, c=YEAR_COLOR: {
        "color": c, "fillColor": c, "fillOpacity": 0.5, "weight": 1
    },
    highlight_function=lambda feature: {"weight": 2},
    tooltip=folium.GeoJsonTooltip(fields=["year"], aliases=["Ano:"]),
).add_to(fg)

fg.add_to(m)

# Layer control AFTER adding layers
folium.LayerControl(position="topright", collapsed=False).add_to(m)

# Fit to layer bounds
m.fit_bounds([[miny, minx], [maxy, maxx]])

In [ ]:
m

In [11]:
files = ["./data/soil_use_2000.shp", "./data/soil_use_2010.shp", "./data/soil_use_2023.shp"]
YEAR_COLS = {"2000": "#e3d917", "2010": "#e32f17", "2023": "#62130a"}


In [12]:
year_groups = []
for path in files:
    try:
        g = read_fix(path)
    except Exception as e:
        print(f"Skipping {path}: {e}")
        continue

    # ensure columns
    if "soil_use" not in g.columns:
        g["soil_use"] = "urbano"

    # derive year from file name if missing/empty
    yr = None
    if "year" in g.columns and g["year"].notna().any():
        try:
            yr = int(g["year"].iloc[0])
        except Exception:
            pass
    if yr is None:
        yr = year_from_path(path)
    if yr is None:
        print(f"Skipping {path}: couldn't determine year")
        continue
    g["year"] = int(yr)                 # normalize to python int
    year_str = str(yr)

    # keep only urbano
    g = g[g["soil_use"].astype(str).str.lower().eq("urbano")].copy()
    if g.empty:
        print(f"Skipping {path}: no 'urbano' features")
        continue

    break


In [14]:
color = YEAR_COLS.get(year_str, "#333333")

In [15]:
color

'#e3d917'

In [13]:
g

class soil_use  year                                           geometry
1      1   urbano  2000  MULTIPOLYGON (((-46.87319 -23.08275, -46.87292...

In [20]:
import json
from folium import GeoJson, FeatureGroup

files = ["./data/soil_use_2000.shp", "./data/soil_use_2010.shp", "./data/soil_use_2023.shp"]
YEAR_COLS = {"2000": "#e3d917", "2010": "#e32f17", "2023": "#62130a"}

year_groups = []
for path in files:
    try:
        g = read_fix(path)
    except Exception as e:
        print(f"Skipping {path}: {e}")
        continue

    # ensure columns + normalize 'year'
    if "soil_use" not in g.columns:
        g["soil_use"] = "urbano"
    yr = g["year"].iloc[0] if "year" in g.columns and g["year"].notna().any() else year_from_path(path)
    if yr is None:
        print(f"Skipping {path}: no year")
        continue
    g["year"] = int(yr)

    # keep only urbano
    g = g[g["soil_use"].astype(str).str.lower().eq("urbano")].copy()
    if g.empty:
        print(f"Skipping {path}: no 'urbano' features")
        continue

    year_str = str(int(g["year"].iloc[0]))
    color = YEAR_COLS.get(year_str, "#333333")

    # proper JSON dict (avoid dtype issues)
    geojson_data = json.loads(g.to_json())

    # create overlay group and add the geojson TO THE GROUP
    fg = FeatureGroup(name=year_str, show=False)
    GeoJson(
        data=geojson_data,
        name=None,  # group holds the name in LayerControl
        style_function=lambda feature, c=color: {
            "color": c, "fillColor": c, "fillOpacity": 0.5, "weight": 1
        },
        highlight_function=lambda feature: {"weight": 2},
        tooltip=folium.GeoJsonTooltip(fields=["year"], aliases=["Ano:"]),
    ).add_to(fg)

    # add the group to the map
    fg.add_to(m)
    year_groups.append((int(year_str), fg))

# show only the latest year by default
if year_groups:
    latest_fg = sorted(year_groups, key=lambda t: t[0])[-1][1]
    latest_fg.show = True

In [ ]:
color = YEAR_COLS.get(year_str, "#333333")

fg = FeatureGroup(name=year_str, show=False)  # will show latest after loop
GeoJson(
    g.__geo_interface__,
    name=None,  # inside the group; group has the name
    style_function=lambda f, c=color: {"color": c, "fillColor": c, "fillOpacity": 0.5, "weight": 1},
    highlight_function=lambda f: {"weight": 2},
    tooltip=folium.GeoJsonTooltip(fields=["year"], aliases=["Ano:"]),
).add_to(m)

year_groups.append((year_str, g, fg))

In [21]:
m

In [ ]:
color = YEAR_COLS.get(year_str, "#333333")
# Use proper JSON dict (avoids numpy dtype serialization issues)
geojson_data = json.loads(g.to_json())

fg = FeatureGroup(name=year_str, show=False)  # we'll enable latest later
GeoJson(
    data=geojson_data,
    name=None,  # group holds the name
    style_function=lambda feature, c=color: {
        "color": c, "fillColor": c, "fillOpacity": 0.5, "weight": 1
    },
    highlight_function=lambda feature: {"weight": 2},
    tooltip=folium.GeoJsonTooltip(fields=["year"], aliases=["Ano:"]),
).add_to(fg)
fg.add_to(m)
year_groups.append((yr, fg))

In [23]:
year_groups = []
for path in files:
    try:
        g = read_fix(path)
    except Exception:
        continue
    # ensure columns
    if "soil_use" not in g.columns:
        g["soil_use"] = "urbano"
    if "year" not in g.columns or g["year"].isna().all():
        g["year"] = year_from_path(path)
    # keep only urbano
    g = g[g["soil_use"].astype(str).str.lower() == "urbano"].copy()
    if g.empty:
        continue

    year_str = str(int(g["year"].iloc[0]))
    color = YEAR_COLS.get(year_str, "#333333")

    fg = FeatureGroup(name=year_str, show=False)  # will show latest after loop
    GeoJson(
        g.__geo_interface__,
        name=None,  # inside the group; group has the name
        style_function=lambda f, c=color: {"color": c, "fillColor": c, "fillOpacity": 0.5, "weight": 1},
        highlight_function=lambda f: {"weight": 2},
        tooltip=folium.GeoJsonTooltip(fields=["year"], aliases=["Ano:"]),
    ).add_to(fg)
    fg.add_to(m)
    year_groups.append((year_str, g, fg))

In [40]:
if year_groups:
    latest_fg = sorted(year_groups, key=lambda t: t[0])[-1][1]
    latest_fg.show = True

In [43]:
fg = folium.FeatureGroup(name=year_str, show=False)  # overlay group
folium.GeoJson(
    data=geojson_data,
    name=None,  # inside group; group carries the name
    style_function=lambda f, c=color: {"color": c, "fillColor": c, "fillOpacity": 0.5, "weight": 1},
    highlight_function=lambda f: {"weight": 2},
    tooltip=folium.GeoJsonTooltip(fields=["year"], aliases=["Ano:"]),
).add_to(fg)
fg.add_to(m)

In [41]:
year_groups

[(2000, <folium.map.FeatureGroup at 0x233d5f9fdf0>),
 (2010, <folium.map.FeatureGroup at 0x233d5f9fce0>),
 (2023, <folium.map.FeatureGroup at 0x233d9296550>)]

In [44]:
m